# Objective:

In this notebook, you will see demo of how [Amazon Q generative SQL in Amazon Redshift Query Editor](https://aws.amazon.com/about-aws/whats-new/2023/11/amazon-redshift-generative-sql-query-editor-preview/) helps to simplify query authoring and increase your productivity by allowing you to express queries in natural language and receive SQL code recommendations.

# Pre-requisites

1. Create Redshift Serverelss workgroup in preview mode.  Please refer this [link](https://docs.aws.amazon.com/redshift/latest/mgmt/serverless-workgroup-preview.html) to create preview wokrgroup.
2. Ensure you setup an IAM role as default IAM role.  Please refer this [link](https://docs.aws.amazon.com/redshift/latest/mgmt/default-iam-role.html#managing-iam-role-console) for instructions.

## Setup Test Data

In this demo we will use the sample TICKIT data which consists of sales to attendants of entertainment events that occurred in 2008.

As first step, let us load the TICKIT data within the sample_data_dev using QEv2. Follow this [doc](https://docs.aws.amazon.com/redshift/latest/mgmt/query-editor-v2-loading.html#query-editor-v2-loading-sample-data) for more details.

Once the data is loaded, Create an empty notebook and choose the Generative SQL icon to open the chat panel.

## SQL prompt #1

Enter the following prompt to generate SQL to verify the number of records in the VENUE table

**How many venues are there?**

In [0]:
SELECT
  COUNT(DISTINCT venueid) AS num_venues
FROM
  tickit.venue

count
------
202

Now let's find out which state has the most no. of venues, choose Regenerate SQL and ask the following question:

**Which state has the most venues?**

In [0]:
SELECT
  venuestate,
  COUNT(venueid) AS num_venues
FROM
  tickit.venue
GROUP BY
  venuestate
ORDER BY
  num_venues DESC
LIMIT
  1

In the SQL cell, choose Run to receive the result of the state with most no. of venues:

venuestate	num_venues
NY	49

Now,lets see if we can find the top five users from Seattle who bought the most number of tickets in 2008. 

**Find the top five users from Seattle who bought the most number of tickets in 2008**

In [0]:
SELECT
  u.userid,
  u.firstname,
  u.lastname,
  COUNT(s.qtysold) AS tickets_bought
FROM
  tickit.users u
  JOIN tickit.sales s ON u.userid = s.buyerid
  JOIN tickit.event e ON s.eventid = e.eventid
  JOIN tickit.date d ON e.dateid = d.dateid
WHERE
  u.city = 'Seattle'
  AND EXTRACT(
    YEAR
    FROM
      d.caldate
  ) = 2008
GROUP BY
  u.userid,
  u.firstname,
  u.lastname
ORDER BY
  tickets_bought DESC
LIMIT
  5

# SQL prompt #2

Generative SQL assistant can make assumptions about what you're asking, even if the schema object doesn't exist in the database.

**How many widgets are there?**

**I was not able to generate any SQL**

# SQL prompt #3

Now lets generate SQL to find the sales for the month of November 2008, enter the following in the prompt:

**How many sales were there in November 2008?**

In [0]:
SELECT
  COUNT(*)
FROM
  tickit.sales s
  JOIN tickit.event e ON s.eventid = e.eventid
  JOIN tickit.date d ON e.dateid = d.dateid
WHERE
  d.month = 'November'
  AND 
  EXTRACT(
    YEAR
    FROM
      d.caldate
  ) = 2008

You realize this is not the result you were expecting.

You notice that the predicate date.month='November' expects the month in the DATE table to be represented by an abbreviation of month name. You change the predicate to d.month='NOV' and rerun the SQL.

In [0]:
SELECT
  COUNT(*)
FROM
  tickit.sales s
  JOIN tickit.event e ON s.eventid = e.eventid
  JOIN tickit.date d ON e.dateid = d.dateid
WHERE
  d.month = 'NOV'
  AND 
  EXTRACT(
    YEAR
    FROM
      d.caldate
  ) = 2008

Now lets see what happens when you try to add data to a table in the connected database, a warning message is returned. Enter the following prompt to generate SQL to inset data into a table:

**Insert into the venue table?**

INSERT
  a row INTO the venue TABLE:

  I detected that this query changes your database. Only run this SQL command if that is appropriate.

The above scenarios illustrated some basic ways to interact with query editor V2 generative SQL. To learn more, please refer to this [blog](https://aws.amazon.com/blogs/aws/amazon-redshift-adds-new-ai-capabilities-to-boost-efficiency-and-productivity/).

## Cleanup

1. Delete Redshift Serverless workgroup. Please refer this [link](https://docs.aws.amazon.com/redshift/latest/mgmt/serverless_delete-workgroup.html) for documentation to delete workgroup.
2. Delete Redshift Serverelss associated namespace. Please refer this [link](https://docs.aws.amazon.com/redshift/latest/mgmt/serverless-console-namespace-delete.html) for documentation to delete workgroup.